In [1]:
import os
import sys
import json
import shutil
import numpy as np
import pandas as pd

In [2]:
# Helper function
def writeProgress(msg, count, total):
    sys.stdout.write(msg + "{:.2%}\r".format(count/total))
    sys.stdout.flush()
    
def newPath(path):
    if not os.path.isdir(path):
        os.mkdir(path)

def read_json(src_path):
    with open(src_path, 'r') as json_file:
        data = json.load(json_file)
    return data

def write_json(data,dst_path):
    with open(dst_path, 'w') as outfile:
        json.dump(data, outfile)

In [3]:
columns = read_json('../../orderedListGenres.json')
print(len(columns), columns)

20 ['Action', 'Adventure', 'Animation', 'Biography', 'Comedy', 'Crime', 'Documentary', 'Drama', 'Family', 'Fantasy', 'History', 'Horror', 'Music', 'Mystery', 'Romance', 'Sci-Fi', 'Sport', 'Thriller', 'War', 'Western']


In [4]:
# 模型輸出儲存的檔案
# SAVE_NAME = 'resnet50_trainable_8e-5_starwars'
HISTORY_SAVE = './history/' + SAVE_NAME + '.csv'
WEIGHTS_SAVE = './weight/' + SAVE_NAME + '.h5'

NameError: name 'SAVE_NAME' is not defined

# ResNet50 Model

In [5]:
# read dataframe
train_df = pd.read_csv('../filename2genreMat.csv')
test_df = pd.read_csv('../poster2genreMat.csv')
print(train_df.shape, test_df.shape)

(37959, 22) (165, 22)


In [6]:
valid_df = train_df.sample(frac = 0.2, random_state = 42)
train_df = train_df.drop(valid_df.index)
print(train_df.shape, valid_df.shape)

(30367, 22) (7592, 22)


In [7]:
from keras.applications import ResNet50
from keras import models
from keras.models import Model
from keras.optimizers import Adam
from keras_preprocessing.image import ImageDataGenerator
from keras import layers
from keras import regularizers, optimizers
# from keras.applications.model import ResNet152

Using TensorFlow backend.


In [8]:
# 資料路徑
DATASET_PATH  = '../IGimg'

# 影像大小
IMAGE_SIZE = (224, 224)

# 影像類別數
NUM_CLASSES = 20

# 若 GPU 記憶體不足，可調降 batch size 或凍結更多層網路
BATCH_SIZE = 32

# Epoch 數
NUM_EPOCHS = 100

In [9]:
datagen=ImageDataGenerator(rescale=1./255.)
test_datagen=ImageDataGenerator(rescale=1./255.)

train_generator=datagen.flow_from_dataframe(dataframe=train_df,
                                            directory=DATASET_PATH,
                                            x_col="filename",
                                            y_col=columns,
                                            batch_size=BATCH_SIZE,
                                            seed=42,
                                            shuffle=True,
                                            class_mode="other",
                                            target_size=IMAGE_SIZE)

valid_generator=test_datagen.flow_from_dataframe(dataframe=valid_df,
                                                 directory=DATASET_PATH,
                                                 x_col="filename",
                                                 y_col=columns,
                                                 batch_size=BATCH_SIZE,
                                                 seed=42,
                                                 shuffle=True,
                                                 class_mode="other",
                                                 target_size=IMAGE_SIZE)

Found 30367 validated image filenames.
Found 7592 validated image filenames.


# Fixed the last Layer from 1000 classes into N classes

In [ ]:
conv_base = ResNet50(weights='imagenet',
                  include_top=False,
                  input_shape=(IMAGE_SIZE[0],IMAGE_SIZE[1],3))
conv_base.summary()

In [ ]:
model = models.Sequential()
model.add(conv_base)        # 將卷積基底視為層加入 Sequential 模型中
model.add(layers.AveragePooling2D(pool_size=(7, 7)))
model.add(layers.Flatten()) # 攤平
model.add(layers.Dense(NUM_CLASSES, activation='sigmoid')) # 增加密集層分類器
model.summary() # 查看模型摘要

In [ ]:
print('This is the number of trainable weights before freezing the conv base:', len(model.trainable_weights))

conv_base.trainable = True

print('This is the number of trainable weights after freezing the conv base:', len(model.trainable_weights))

In [ ]:
model.compile(optimizer=Adam(lr=8e-5),
              loss='binary_crossentropy',
              metrics=['acc'])
model.summary()

# Training Model

In [ ]:
STEP_SIZE_TRAIN = train_generator.n // train_generator.batch_size
STEP_SIZE_VALID = valid_generator.n // valid_generator.batch_size

In [ ]:
# 訓練模型
from keras.callbacks import EarlyStopping
callbacks = [EarlyStopping(monitor='val_loss')]

history = model.fit_generator(generator = train_generator,
                              steps_per_epoch = STEP_SIZE_TRAIN,
                              validation_data = valid_generator,
                              validation_steps = STEP_SIZE_VALID,
                              epochs = NUM_EPOCHS,
                              callbacks=callbacks)

In [ ]:
# 儲存訓練好的模型
model.save(WEIGHTS_SAVE)

In [ ]:
# save history
acc = history.history['acc']
val_acc = history.history['val_acc']
loss = history.history['loss']
val_loss = history.history['val_loss']
epochs = range(1, len(acc) + 1)

his_df = pd.DataFrame(data = {
    'Epoch' : epochs,
    'Loss' : loss,
    'Acc' : acc,
    'Val_loss' : val_loss,
    'Val_acc' : val_acc
})
his_df = his_df[['Epoch', 'Loss', 'Acc', 'Val_loss', 'Val_acc']]
his_df.to_csv(HISTORY_SAVE, index = False)

# Plot acc & loss

In [ ]:
# 繪製結果
import matplotlib.pyplot as plt

plt.figure()

plt.plot(epochs, acc, 'b', label='Training acc')
plt.plot(epochs, val_acc, 'r', label='Validation acc')
plt.title('Training and validation accuracy')
plt.legend()

plt.show()

plt.figure()

plt.plot(epochs, loss, 'b', label='Training loss')
plt.plot(epochs, val_loss, 'r', label='Validation loss')
plt.title('Training and validation loss')
plt.legend()

plt.show()

# Testing

### Testing set: Poster

In [ ]:
SAVE_NAME = SAVE_NAME + '_poster'

In [ ]:
test_df = pd.read_csv('../poster2genreMat.csv')
test_df

In [ ]:
DATASET_PATH = '../Poster'

In [ ]:
test_generator=test_datagen.flow_from_dataframe(dataframe=test_df,
                                                directory=DATASET_PATH,
                                                x_col="filename",
                                                batch_size=1,
                                                seed=42,
                                                shuffle=False,
                                                class_mode=None,
                                                target_size=IMAGE_SIZE)

In [ ]:
STEP_SIZE_TEST = test_generator.n // test_generator.batch_size

In [ ]:
test_generator.reset()
pred=model.predict_generator(test_generator,
                             steps=STEP_SIZE_TEST,
                             verbose=1)

# Output

In [ ]:
pred.shape

In [ ]:
predictions = pred

results=pd.DataFrame(predictions, columns=columns)
results["filename"] = test_generator.filenames
ordered_cols = ["filename"] + columns
results = results[ordered_cols] #To get the same column order
results.to_csv("./output/"+ SAVE_NAME + "_result.csv",index=False)

## Label top n dynamic

In [ ]:
true_df = test_df

In [ ]:
results = pd.read_csv("./output/"+ SAVE_NAME + "_result.csv")
results

In [ ]:
labels = read_json('../../genresDic.json')

In [ ]:
def countAcc(predList, trueList):
    fraction = 0
    denominator = len(trueList)
    for g in predList:
        if g in trueList:
            fraction += 1 
    return fraction / denominator

In [ ]:
li = []
for i, row in true_df.iterrows():
    username = row['filename']
    if username == results.loc[i,:]['filename']: # username equals
        print(i, username)
        accname = username.split('.')[0]
        truth = labels[accname]
        numTrue = sum(row[2:])
        print('count:', numTrue)
        
        s = results.loc[i,:][1:]
        top_n = s.sort_values(ascending=False)[:numTrue]
        inList = list(top_n.index)
        
        onehot = []
        for g in columns:
            onehot.append(int(g in inList))
            
        accu = countAcc(inList, truth)
        print(accu, inList, truth)
        
        appList = [username, accu, truth, inList] + onehot
        li.append(appList)
        

In [ ]:
acc_df = pd.DataFrame(li, columns = ['username', 'acc', 'truth', 'top_n'] + columns)
acc_df

In [ ]:
acc_df.to_csv("./output/"+ SAVE_NAME + "_bi.csv", index = 0)

In [ ]:
acc_df['acc'].mean()

# Feature Extraction
## 測試reload model準確度

In [28]:
DATASET_PATH  = '../IGimg'
# train_df = pd.read_csv('../filename2genreMat.csv')
train_df = pd.read_csv('./output/less_7e-01.csv')
print(train_df.shape)
train_df

(34761, 21)


filename    Action  Adventure  Animation  Biography  \
0      21bridgesmovie_22217.jpg  0.376427   0.001377   0.000341   0.001846   
1      21bridgesmovie_22218.jpg  0.994637   0.000518   0.000833   0.004196   
2      21bridgesmovie_22219.jpg  0.436303   0.000693   0.000449   0.000460   
3      21bridgesmovie_22220.jpg  0.346905   0.020233   0.000223   0.001022   
4      21bridgesmovie_22221.jpg  0.598846   0.020068   0.011229   0.002074   
...                         ...       ...        ...        ...        ...   
34756       zombieland_7839.jpg  0.183466   0.018547   0.000766   0.015293   
34757       zombieland_7840.jpg  0.345522   0.106106   0.017836   0.021062   
34758       zombieland_7841.jpg  0.063304   0.002134   0.000388   0.287875   
34759       zombieland_7842.jpg  0.952945   0.001020   0.026686   0.000214   
34760       zombieland_7843.jpg  0.968902   0.017898   0.006868   0.000423   

         Comedy     Crime  Documentary     Drama        Family  ...   History  \
0      0.017973  0.972387     0.000248  0.999929  5.245209e-06  ...  0.001194   
1      0.003593  0.998304     0.000551  0.992287  1.788139e-07  ...  0.004454   
2      0.000094  0.977469     0.000171  0.999988  5.364418e-07  ...  0.001022   
3      0.015805  0.911007     0.000067  0.983264  1.770258e-05  ...  0.033229   
4      0.073472  0.885954     0.002687  0.984622  7.396936e-05  ...  0.142680   
...         ...       ...          ...       ...           ...  ...       ...   
34756  0.897609  0.016318     0.018880  0.050032  2.655387e-05  ...  0.006629   
34757  0.998469  0.000304     0.053013  0.403472  4.184246e-05  ...  0.002718   
34758  0.605060  0.388846     0.002164  0.758197  2.205372e-05  ...  0.002585   
34759  0.990958  0.047280     0.000211  0.012385  4.768372e-07  ...  0.000251   
34760  0.979940  0.000340     0.000046  0.010735  1.460314e-06  ...  0.000167   

         Horror     Music   Mystery   Romance    Sci-Fi     Sport  Thriller  \
0      0.000195  0.000399  0.001006  0.001320  0.001614  0.033926  0.000165   
1      0.001358  0.005030  0.003433  0.000068  0.007294  0.000104  0.002123   
2      0.000224  0.000068  0.000119  0.106868  0.000182  0.013787  0.008738   
3      0.000764  0.003675  0.001625  0.004505  0.009784  0.001231  0.004782   
4      0.035371  0.021160  0.005252  0.003960  0.012384  0.005979  0.010176   
...         ...       ...       ...       ...       ...       ...       ...   
34756  0.996807  0.035176  0.003944  0.000495  0.007747  0.000806  0.001157   
34757  0.905482  0.002339  0.000058  0.001520  0.225363  0.000236  0.000813   
34758  0.710738  0.014425  0.002585  0.021587  0.001550  0.000121  0.003501   
34759  0.937793  0.000916  0.000783  0.002178  0.003021  0.000343  0.005882   
34760  0.950592  0.001193  0.001686  0.000303  0.004750  0.001494  0.007023   

            War   Western  
0      0.000469  0.000013  
1      0.000724  0.000020  
2      0.000154  0.000011  
3      0.000030  0.000027  
4      0.001693  0.001547  
...         ...       ...  
34756  0.000535  0.000144  
34757  0.000010  0.000002  
34758  0.000035  0.000124  
34759  0.000006  0.000002  
34760  0.000341  0.000002  

[34761 rows x 21 columns]

In [ ]:
# SAVE_NAME = 'test'
# DATASET_PATH = '../Poster'

# test_df = pd.read_csv('../poster2genreMat.csv')
# print(test_df.shape)
# test_df

In [29]:
WEIGHTS_LOAD = './weight/resnet50_trainable_9e-5_newdata.h5'

from keras.models import load_model

model = load_model(WEIGHTS_LOAD)

In [30]:
model.summary()

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
resnet50 (Model)             (None, 7, 7, 2048)        23587712  
_________________________________________________________________
flatten_2 (Flatten)          (None, 100352)            0         
_________________________________________________________________
dense_3 (Dense)              (None, 256)               25690368  
_________________________________________________________________
dense_4 (Dense)              (None, 20)                5140      
Total params: 49,283,220
Trainable params: 49,230,100
Non-trainable params: 53,120
_________________________________________________________________


In [31]:
test_generator=test_datagen.flow_from_dataframe(dataframe=train_df,#test_df
                                                directory=DATASET_PATH,
                                                x_col="filename",
                                                batch_size=1,
                                                seed=42,
                                                shuffle=False,
                                                class_mode=None,
                                                target_size=IMAGE_SIZE)

Found 34761 validated image filenames.


In [32]:
STEP_SIZE_TEST = test_generator.n // test_generator.batch_size

In [33]:
test_generator.reset()
pred=model.predict_generator(test_generator,
                             steps=STEP_SIZE_TEST,
                             verbose=1)

34761/34761 [==============================] - 300s 9ms/step


In [34]:
pred.shape

(34761, 20)

In [35]:
SAVE_NAME = 'less_7e-01'

In [36]:
predictions = pred

results=pd.DataFrame(predictions, columns=columns)
results["filename"] = test_generator.filenames
ordered_cols = ["filename"] + columns
results = results[ordered_cols] #To get the same column order
results.to_csv("./output/"+ SAVE_NAME + "_result.csv",index=False)

In [37]:
true_df = train_df #test_df
labels = read_json('../../genresDic.json')

In [38]:
def countAcc(predList, trueList):
    fraction = 0
    denominator = len(trueList)
    for g in predList:
        if g in trueList:
            fraction += 1 
    return fraction / denominator

In [39]:
li = []
for i, row in true_df.iterrows():
    username = row['filename']
    if username == results.loc[i,:]['filename']: # username equals
        print(i, username)
        accname = username.split('_')[0] #username.split('.')[0]
        if accname == 'downtonabbey':
            accname = 'downtonabbey_official'
        truth = labels[accname]
        print(truth)
        numTrue = len(truth)
        print('count:', numTrue)
        
        s = results.loc[i,:][1:]
        top_n = s.sort_values(ascending=False)[:numTrue]
        inList = list(top_n.index)
        
        onehot = []
        for g in columns:
            onehot.append(int(g in inList))
            
        accu = countAcc(inList, truth)
        print(accu, inList, truth)
        
        appList = [username, accu, truth, inList] + onehot
        li.append(appList)

0 21bridgesmovie_22217.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Drama', 'Crime', 'Action'] ['Action', 'Crime', 'Drama']
1 21bridgesmovie_22218.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Crime', 'Action', 'Drama'] ['Action', 'Crime', 'Drama']
2 21bridgesmovie_22219.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Drama', 'Crime', 'Action'] ['Action', 'Crime', 'Drama']
3 21bridgesmovie_22220.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Drama', 'Crime', 'Action'] ['Action', 'Crime', 'Drama']
4 21bridgesmovie_22221.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Drama', 'Crime', 'Action'] ['Action', 'Crime', 'Drama']
5 21bridgesmovie_22222.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Crime', 'Action', 'Drama'] ['Action', 'Crime', 'Drama']
6 21bridgesmovie_22223.jpg
['Action', 'Crime', 'Drama']
count: 3
0.6666666666666666 ['Drama', 'Action', 'Horror'] ['Action', 'Crime', 'Drama']
7 21bridgesmovie_22224.jpg
['Action', 'Crime', 'Drama']
count: 3
1.0 ['Drama', 'Action', 'Crime

1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
163 abeautifuldaymovie_14572.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
164 abeautifuldaymovie_14573.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
165 abeautifuldaymovie_14574.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
166 abeautifuldaymovie_14575.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
167 abeautifuldaymovie_14576.jpg
['Biography', 'Drama']
count: 2
1.0 ['Biography', 'Drama'] ['Biography', 'Drama']
168 abeautifuldaymovie_14577.jpg
['Biography', 'Drama']
count: 2
1.0 ['Biography', 'Drama'] ['Biography', 'Drama']
169 abeautifuldaymovie_14578.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
170 abeautifuldaymovie_14579.jpg
['Biography', 'Drama']
count: 2
1.0 ['Drama', 'Biography'] ['Biography', 'Drama']
171 abeautifuldaymovie_14580.j

1.0 ['Comedy', 'Adventure', 'Animation'] ['Adventure', 'Animation', 'Comedy']
329 abominablemovie_7350.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Comedy', 'Adventure', 'Animation'] ['Adventure', 'Animation', 'Comedy']
330 abominablemovie_7351.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Adventure', 'Comedy', 'Animation'] ['Adventure', 'Animation', 'Comedy']
331 abominablemovie_7352.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Adventure', 'Comedy', 'Animation'] ['Adventure', 'Animation', 'Comedy']
332 abominablemovie_7353.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Adventure', 'Comedy', 'Animation'] ['Adventure', 'Animation', 'Comedy']
333 abominablemovie_7354.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Comedy', 'Adventure', 'Animation'] ['Adventure', 'Animation', 'Comedy']
334 abominablemovie_7355.jpg
['Adventure', 'Animation', 'Comedy']
count: 3
1.0 ['Adventure', 'Animation', 'Comedy'] ['Adventure', 'Animation', 'Comedy']
335 

1.0 ['Mystery', 'Adventure', 'Drama'] ['Adventure', 'Drama', 'Mystery']
496 adastramovie_3378.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
0.3333333333333333 ['Adventure', 'Sci-Fi', 'Action'] ['Adventure', 'Drama', 'Mystery']
497 adastramovie_3379.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
0.6666666666666666 ['Adventure', 'Drama', 'Action'] ['Adventure', 'Drama', 'Mystery']
498 adastramovie_3380.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
1.0 ['Mystery', 'Adventure', 'Drama'] ['Adventure', 'Drama', 'Mystery']
499 adastramovie_3381.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
0.6666666666666666 ['Adventure', 'Mystery', 'Fantasy'] ['Adventure', 'Drama', 'Mystery']
500 adastramovie_3383.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
0.6666666666666666 ['Drama', 'Mystery', 'Fantasy'] ['Adventure', 'Drama', 'Mystery']
501 adastramovie_3384.jpg
['Adventure', 'Drama', 'Mystery']
count: 3
1.0 ['Drama', 'Mystery', 'Adventure'] ['Adventure', 'Drama', 'Mystery']
502 adastramovie_3385.j

1.0 ['Drama', 'Adventure', 'Comedy'] ['Adventure', 'Comedy', 'Drama']
664 adogsjourneymovie_37750.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
1.0 ['Drama', 'Comedy', 'Adventure'] ['Adventure', 'Comedy', 'Drama']
665 adogsjourneymovie_37751.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
0.6666666666666666 ['Drama', 'Adventure', 'Mystery'] ['Adventure', 'Comedy', 'Drama']
666 adogsjourneymovie_37752.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
1.0 ['Adventure', 'Comedy', 'Drama'] ['Adventure', 'Comedy', 'Drama']
667 adogsjourneymovie_37753.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
1.0 ['Drama', 'Comedy', 'Adventure'] ['Adventure', 'Comedy', 'Drama']
668 adogsjourneymovie_37754.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
1.0 ['Drama', 'Comedy', 'Adventure'] ['Adventure', 'Comedy', 'Drama']
669 adogsjourneymovie_37755.jpg
['Adventure', 'Comedy', 'Drama']
count: 3
1.0 ['Drama', 'Comedy', 'Adventure'] ['Adventure', 'Comedy', 'Drama']
670 adogsjourneymovie_37756.jpg
['Adventure', 'Com

...

0.0 ['Drama', 'Music', 'Romance'] ['Action', 'Adventure', 'Sci-Fi']
34084 xmenmovies_2121.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Adventure', 'Action', 'Fantasy'] ['Action', 'Adventure', 'Sci-Fi']
34085 xmenmovies_2122.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Comedy', 'Action', 'Adventure'] ['Action', 'Adventure', 'Sci-Fi']
34086 xmenmovies_2123.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Action', 'Adventure', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34087 xmenmovies_2124.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Sci-Fi', 'Adventure', 'Action'] ['Action', 'Adventure', 'Sci-Fi']
34088 xmenmovies_2125.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Action', 'Adventure', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34089 xmenmovies_2126.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.3333333333333333 ['Action', 'Comedy', 'Drama'] ['Action', 'Adventure', 'Sci-Fi']
34090 xmenmovies_2127.jpg
['Action', 'Advent

0.3333333333333333 ['Adventure', 'Drama', 'Comedy'] ['Action', 'Adventure', 'Sci-Fi']
34192 xmenmovies_780.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Adventure', 'Action', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34193 xmenmovies_781.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Adventure', 'Fantasy', 'Action'] ['Action', 'Adventure', 'Sci-Fi']
34194 xmenmovies_782.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Romance', 'Adventure', 'Action'] ['Action', 'Adventure', 'Sci-Fi']
34195 xmenmovies_783.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Action', 'Drama', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34196 xmenmovies_784.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Adventure', 'Sci-Fi', 'Action'] ['Action', 'Adventure', 'Sci-Fi']
34197 xmenmovies_785.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.0 ['Drama', 'Romance', 'Crime'] ['Action', 'Adventure', 'Sci-Fi']
34198 xmenmovies_786.jpg
['Action',

34317 xmenmovies_929.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Romance', 'Action', 'Adventure'] ['Action', 'Adventure', 'Sci-Fi']
34318 xmenmovies_930.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Adventure', 'Action', 'Fantasy'] ['Action', 'Adventure', 'Sci-Fi']
34319 xmenmovies_931.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.6666666666666666 ['Adventure', 'Action', 'Comedy'] ['Action', 'Adventure', 'Sci-Fi']
34320 xmenmovies_932.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Sci-Fi', 'Adventure', 'Action'] ['Action', 'Adventure', 'Sci-Fi']
34321 xmenmovies_933.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Adventure', 'Action', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34322 xmenmovies_935.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
1.0 ['Action', 'Adventure', 'Sci-Fi'] ['Action', 'Adventure', 'Sci-Fi']
34323 xmenmovies_936.jpg
['Action', 'Adventure', 'Sci-Fi']
count: 3
0.3333333333333333 ['Romance', 'Adventure', '

1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34448 yardiefilm_9159.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34449 yardiefilm_9160.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34450 yardiefilm_9161.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34451 yardiefilm_9162.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34452 yardiefilm_9163.jpg
['Crime', 'Drama']
count: 2
1.0 ['Crime', 'Drama'] ['Crime', 'Drama']
34453 yardiefilm_9164.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34454 yardiefilm_9165.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34455 yardiefilm_9166.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34456 yardiefilm_9167.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama']
34457 yardiefilm_9168.jpg
['Crime', 'Drama']
count: 2
1.0 ['Drama', 'Crime'] ['Crime', 'Drama'

1.0 ['Comedy', 'Horror', 'Action'] ['Action', 'Comedy', 'Horror']
34596 zombieland_7671.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Horror', 'Action', 'Comedy'] ['Action', 'Comedy', 'Horror']
34597 zombieland_7672.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Horror', 'Comedy', 'Action'] ['Action', 'Comedy', 'Horror']
34598 zombieland_7673.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Comedy', 'Horror', 'Action'] ['Action', 'Comedy', 'Horror']
34599 zombieland_7674.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Horror', 'Comedy', 'Action'] ['Action', 'Comedy', 'Horror']
34600 zombieland_7675.jpg
['Action', 'Comedy', 'Horror']
count: 3
0.6666666666666666 ['Comedy', 'Horror', 'Drama'] ['Action', 'Comedy', 'Horror']
34601 zombieland_7676.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Comedy', 'Action', 'Horror'] ['Action', 'Comedy', 'Horror']
34602 zombieland_7677.jpg
['Action', 'Comedy', 'Horror']
count: 3
1.0 ['Horror', 'Action', 'Comedy'] ['Action', 'Comedy', 'Horro

In [40]:
acc_df = pd.DataFrame(li, columns = ['username', 'acc', 'truth', 'top_n'] + columns)
acc_df['acc'].mean()

0.8774057132994071

In [41]:
acc_df

username       acc                     truth  \
0      21bridgesmovie_22217.jpg  1.000000    [Action, Crime, Drama]   
1      21bridgesmovie_22218.jpg  1.000000    [Action, Crime, Drama]   
2      21bridgesmovie_22219.jpg  1.000000    [Action, Crime, Drama]   
3      21bridgesmovie_22220.jpg  1.000000    [Action, Crime, Drama]   
4      21bridgesmovie_22221.jpg  1.000000    [Action, Crime, Drama]   
...                         ...       ...                       ...   
34756       zombieland_7839.jpg  1.000000  [Action, Comedy, Horror]   
34757       zombieland_7840.jpg  0.666667  [Action, Comedy, Horror]   
34758       zombieland_7841.jpg  0.666667  [Action, Comedy, Horror]   
34759       zombieland_7842.jpg  1.000000  [Action, Comedy, Horror]   
34760       zombieland_7843.jpg  1.000000  [Action, Comedy, Horror]   

                          top_n  Action  Adventure  Animation  Biography  \
0        [Drama, Crime, Action]       1          0          0          0   
1        [Crime, Action, Drama]       1          0          0          0   
2        [Drama, Crime, Action]       1          0          0          0   
3        [Drama, Crime, Action]       1          0          0          0   
4        [Drama, Crime, Action]       1          0          0          0   
...                         ...     ...        ...        ...        ...   
34756  [Horror, Comedy, Action]       1          0          0          0   
34757   [Comedy, Horror, Drama]       0          0          0          0   
34758   [Drama, Horror, Comedy]       0          0          0          0   
34759  [Comedy, Action, Horror]       1          0          0          0   
34760  [Comedy, Action, Horror]       1          0          0          0   

       Comedy  Crime  ...  History  Horror  Music  Mystery  Romance  Sci-Fi  \
0           0      1  ...        0       0      0        0        0       0   
1           0      1  ...        0       0      0        0        0       0   
2           0      1  ...        0       0      0        0        0       0   
3           0      1  ...        0       0      0        0        0       0   
4           0      1  ...        0       0      0        0        0       0   
...       ...    ...  ...      ...     ...    ...      ...      ...     ...   
34756       1      0  ...        0       1      0        0        0       0   
34757       1      0  ...        0       1      0        0        0       0   
34758       1      0  ...        0       1      0        0        0       0   
34759       1      0  ...        0       1      0        0        0       0   
34760       1      0  ...        0       1      0        0        0       0   

       Sport  Thriller  War  Western  
0          0         0    0        0  
1          0         0    0        0  
2          0         0    0        0  
3          0         0    0        0  
4          0         0    0        0  
...      ...       ...  ...      ...  
34756      0         0    0        0  
34757      0         0    0        0  
34758      0         0    0        0  
34759      0         0    0        0  
34760      0         0    0        0  

[34761 rows x 24 columns]

## 萃取97部電影imdb的feature

### Poster Feature Vector

In [ ]:
test_generator

In [ ]:
extract_layer = Model(inputs=model.input,
                      outputs=model.get_layer('flatten_1').output)
#以这个model的预测值作为输出
extract_output = extract_layer.predict_generator(test_generator,
                                                 steps=STEP_SIZE_TEST,
                                                 verbose=1)
print(extract_output.shape)

In [ ]:
idx = test_generator.filenames
print(len(idx), idx)

In [ ]:
res=pd.DataFrame(extract_output, index = idx)
res

In [ ]:
res.to_csv("./output/PosterFeatureVec.csv", header=False)

### IG images

In [ ]:
DATASET_PATH  = '../IGimg'
train_df = pd.read_csv('../filename2genreMat.csv')
train_df

In [ ]:
train_generator=datagen.flow_from_dataframe(dataframe=train_df,
                                            directory=DATASET_PATH,
                                            x_col="filename",
                                            batch_size=1,
                                            seed=42,
                                            shuffle=False,
                                            class_mode=None,
                                            target_size=IMAGE_SIZE)

In [ ]:
STEP_SIZE_TRAIN = train_generator.n // train_generator.batch_size
print(STEP_SIZE_TRAIN)

In [ ]:
extract_layer = Model(inputs=model.input,
                      outputs=model.get_layer('flatten_1').output)
#以这个model的预测值作为输出
extract_output = extract_layer.predict_generator(train_generator,
                                                 steps=STEP_SIZE_TRAIN,
                                                 verbose=1)
print(extract_output.shape)

In [ ]:
idx = train_generator.filenames
print(len(idx), idx)

In [ ]:
res=pd.DataFrame(extract_output, index = idx)
res

In [ ]:
res.to_csv("./output/IGimgFeatureVec.csv", header=False)